# MILP: Waterborne Urban Logistics in Amsterdam

## Problem and model recap

Amsterdam’s historic center is served by many Hotels, Restaurants and Cafés (HoReCa) that require frequent deliveries of food supplies. Traditional truck-based logistics contributes to congestion, emissions, and stress on fragile quay walls and bridges. To reduce these impacts, the city explores a logistics system that uses urban waterways for bulk transport and light vehicles (LVs) for last-mile delivery. In this system, goods are transported by vessel from a consolidation hub to Transfer Points (TPs) along the canal network. From these TPs, supplies are delivered by LVs to nearby HoReCa demand zones.

Your task is to design this network optimally by answering two key questions:
1. Which transfer points should be established?
2. How should HoReCa demand be assigned to the selected transfer points?

Each TP has a fixed establishment cost, a limited handling capacity, and a geographic location.
Each demand zone has a known weekly demand for supplies, and a specific geographic location.
Serving demand through a TP incurs transport costs (water + road) and and associated greenhouse gas emissions.

The challenge is to find a configuration of open TPs and demand assignments that:
* satisfies all HoReCa demand,
* respects TP capacities and planning constraints,
* stays within budget and siting limits,
* and minimises total system costs.

This forms a location-allocation MILP problem where strategic decisions (which TPs to open) interact with operational decisions (how demand flows are distributed).

### Parameters

- $d_i$: demand at zone $i$
- ${cap}_j$: capacity of TP $j$ 
- $f_j$: fixed cost of establishing TP $j$
- $t^{\text{water}}_{0j}$: water distance from consolidation hub to TP $j$  
- $t^{\text{road}}_{ij}$: LV road distance from TP $j$ to zone $i$ 
- $c^{water}$: unit water transport cost  
- $c^{road}$: unit road transport cost 
- $e^{water}$: unit emission factor for vessels  
- $e^{road}$: unit emission factor for LVs  
- $D_{max}$: maximum delivery distance  
- $\delta_{ij}$: if TP $j$ is allowed to serve zone $i$ ($ t^{\text{road}}_{ij} \leq D_{max}$)
- $B$: investment budget  
- $K$: maximum number of TPs allowed 
- $\lambda \ge 0$: emission penalty factor  


### Decision variables

- $x_j \in \{0,1\}$: 1 if TP $j$ is opened; 0 otherwise  
- $y_{ij} \geq 0$: flow from TP $j$ to demand zone $i$


### Model
$$\begin{align*}
min \quad  & Z = {\sum_{j \in J} f_j\,x_j}+{\sum_{(i,j)\in A}{CT}_{ij}.y_{ij}}+\lambda{\sum_{(i,j)\in A}{Em}_{ij}.y_{ij}}\\
\text{s.t.} \quad \\
& \sum_{j \in J} y_{ij} = d_i
\qquad \forall i \in I\\
& \sum_{i \in I} y_{ij} \leq {cap}_jx_j
\qquad \forall j \in J\\
& \sum_{j \in J} f_j x_j \leq B\\
& \sum_{j \in J} x_j \leq K\\
& y_{ij} \leq M \delta_{ij} \qquad \forall i \in I,\forall j \in J\\
& x_{j} \in \{0,1\}\\
& y_{ij} \geq 0
\end{align*}$$


## Data description

In this assignment you will work with pre-processed data for Amsterdam’s historic city center. The raw inputs (exact locations and demands of individual HoReCa businesses, and candidate Transfer Points) have been processed into two main components: HoReCa demand zones and a Smaller set of candidate TPs. 

You'll work with two instances:
- a small instance with 15 demand zones and 10 TPs  
- a larger instance with 300 demand zones and 36 TPs  

You will receive separate data for each instance.

---

### HoReCa demand zones

The historic center contains more than 1500 individual HoReCa entities. To keep the optimisation model tractable and interpretable, these are grouped into HoReCa demand zones using spatial clustering:

- Each HoReCa entity has a known longitude, latitude, and estimated weekly demand (derived from [Pourmohammadzia and Koningsveld (2024)](https://www.sciencedirect.com/science/article/pii/S2210670724001628)). Entities are clustered into $n$ groups (e.g. $n=15$ for the small instance). For each cluster, the centroid is taken as the demand zone locationa and the sum of demands of all entities in that cluster gives the zone’s total weekly demand ($d_i$).

![](https://github.com/TUDelft-MUDE/source-files/raw/main/file/demand_zones.png)
---

### Candidate Transfer Points (TPs)

The Municipality of Amsterdam (MoA) has identified 36 potential locations for HoReCa Transfer Points (TPs) along the canals, and classified them into three categories: Spacious, Moderate, and Poor. For the optimisation experiments, we select:
- Small instance: 10 TPs (a subset of the 36, spatially distributed)
- Large instance: 36 TPs

For each TP, we define:

- Its geographic location (longitude, latitude)
- A capacity ($cap_j$) (maximum weekly throughput), which depends on its category
- A fixed establishment cost ($f_j$), which depends on its category 

---

### Distance-based feasibility and service limits

We define a central consolidation hub (outside the historic centre) as the origin of all vessel flows. Using the coordinates of the hub, TPs, and demand zones, we compute:

- $t^{water}_{0j}$: water distance (in km) from the hub to TP $j$  
- $t^{road}_{ij}$ : road distance (in km) from TP $j$ to demand zone $i$

We also impose a maximum last-mile distance for LVs: $D_{max} = 2$

We encode service feasibility with: $
\delta_{ij} =
\begin{cases}
1 & \text{if } t^{road}_{ij} \le D_{max} \\
0 & \text{otherwise}
\end{cases}
$

---

### Global parameters

In addition to zone and TP data, we use a few global parameters that are common to all instances.

#### Transport cost parameters

We model cost per unit of demand per kilometre. These are derived from estimated cost-per-vehicle-km and typical vehicle capacities. For this assignment, we use $c^{road} = 0.03$ and $c^{water} = 0.01$ €/unit/km.
 

#### Emission parameters

Similarly, we define emission factors per unit of demand per kilometre. For this assignment, we use $e^{road} = 0.045$ and $e^{water} = 0.015$ CO₂/unit/km.

These values are consistent with literature values for diesel trucks, LVs, and inland vessels, scaled down to “per unit” (pallet-equivalent).

---

### Planning limits

For each instance, we also specify Budget and Maximum number of TPs. Suggested values are:

- Small instance: $B = 1000$ and $K = 10$
- Large instance: $B = 2000$ and $K = 20$

Finally, we will experiment with different values of the *emission penalty factor*: $\lambda \in \{1, 5, 10, 15\} $


<div style="background-color:#AABAB2; color: black; vertical-align: middle; padding:15px; margin: 10px; border-radius: 10px; width: 95%">

<b>Task 1: (small instance)</b>   

Run the cells below to:

<ul>
<li>Import the required Python packages</li>
<li>Load the required data</li>
<li>Transform the data into the inputs required for the model</li>
</ul>

**Note:** You are not expected to fully understand all details of the data processing code at this stage. These cells make use of Pandas and DataFrames, which will be explained in more depth later in the course. For now, focus on how the processed data becomes structured inputs for the optimization.

</div>

In [1]:
# Task 1 – small instance
# Step 1: Import required packages

import math
import pandas as pd
import os
from urllib.request import urlretrieve


<div style="background-color:#facb8e; color: black; padding:15px; margin: 10px; border-radius: 10px; width: 95%;">

**Note:** If you do not have `pandas`, `numpy`, and `math` already installed, you can simply use: <pre>`pip install YOUR_PACKAGE_NAME`</pre>

</div>

In [2]:
# Task 1 – small instance
# Step 2: Load the small-instance data (demand zones + TPs)

def findfile(fname):
    if not os.path.isfile(fname):
        print(f"Downloading {fname}...")
        urlretrieve('https://github.com/TUDelft-MUDE/source-files/raw/main/file/'+fname, fname)

findfile("GA_2_5_data.xlsx")

data_file = "GA_2_5_data.xlsx"

# Read only the small sheets
df_sml_dem = pd.read_excel(data_file, sheet_name="Small_Demand")
df_sml_tp  = pd.read_excel(data_file, sheet_name="Small_TP")

# Standardise column names
df_sml_dem = df_sml_dem.rename(columns={
    "number": "zone_id",
    "latitude": "lat",
    "longitude": "lon",
    "demand": "demand"
})

df_sml_tp = df_sml_tp.rename(columns={
    "number": "tp_id",
    "latitude": "lat",
    "longitude": "lon",
    "capacity": "capacity",
    "establishment_cost": "fixed_cost"
})

print("Small demand zones:", df_sml_dem.shape[0])
print("Small TPs:", df_sml_tp.shape[0])

display(df_sml_dem.head())
display(df_sml_tp.head())

Small demand zones: 15
Small TPs: 10


zone_id        lat       lon  demand
0        1  52.382283  4.887742     136
1        2  52.363788  4.901048     160
2        3  52.373034  4.882087     200
3        4  52.371771  4.895139     202
4        5  52.368375  4.911447     142

tp_id        lat       lon  capacity  fixed_cost
0      1  52.374000  4.876000       780         150
1      2  52.383215  4.892515       780         150
2      3  52.362109  4.882394       395         125
3      4  52.370470  4.888409       395         125
4      5  52.362614  4.901024       395         125

In [3]:
# Task 1 – small instance
# Step 3: Create index sets and basic parameters for the small instance

# Index sets
I_sml = df_sml_dem["zone_id"].tolist()  # demand zones
J_sml = df_sml_tp["tp_id"].tolist()     # transfer points

# Demand, capacity, fixed cost
d_sml   = dict(zip(df_sml_dem["zone_id"], df_sml_dem["demand"]))
cap_sml = dict(zip(df_sml_tp["tp_id"], df_sml_tp["capacity"]))
f_sml   = dict(zip(df_sml_tp["tp_id"], df_sml_tp["fixed_cost"]))

print("\nTotal demand (small):", sum(d_sml.values()))
print("Total TP capacity (small):", sum(cap_sml.values()))


Total demand (small): 3121
Total TP capacity (small): 4135


In [4]:
# Task 1 – small instance
# Step 4: Define hub location and distance function

# Consolidation hub coordinates (given)
hub_lat = 52.405141
hub_lon = 4.872129

def haversine_km(lon1, lat1, lon2, lat2):
    """
    Compute great-circle distance between two points on Earth (km).
    Inputs and outputs are in decimal degrees and kilometers.
    """
    # convert degrees to radians
    lon1_rad, lat1_rad = math.radians(lon1), math.radians(lat1)
    lon2_rad, lat2_rad = math.radians(lon2), math.radians(lat2)

    dlon = lon2_rad - lon1_rad
    dlat = lat2_rad - lat1_rad

    a = math.sin(dlat/2.0)**2 + math.cos(lat1_rad)*math.cos(lat2_rad)*math.sin(dlon/2.0)**2
    c = 2 * math.asin(math.sqrt(a))
    R = 6371.0  # Earth radius in km
    return R * c

In [5]:
# Task 1 – small instance
# Step 5: Compute water distances t0j_water from hub to each TP (small instance)

t0j_water_sml = {}   # key = tp_id, value = distance (km)

for _, row in df_sml_tp.iterrows():
    j = row["tp_id"]
    dist_km = haversine_km(hub_lon, hub_lat, row["lon"], row["lat"])
    t0j_water_sml[j] = dist_km

print("Example t0j_water_sml (first 5 TPs):")
for j in list(t0j_water_sml.keys())[:5]:
    print(f"  TP {j}: {t0j_water_sml[j]:.2f} km from hub")

Example t0j_water_sml (first 5 TPs):
  TP 1.0: 3.47 km from hub
  TP 2.0: 2.80 km from hub
  TP 3.0: 4.84 km from hub
  TP 4.0: 4.01 km from hub
  TP 5.0: 5.12 km from hub


In [6]:
# Task 1 – small instance
# Step 6: Compute road distances tij_road between TPs and demand zones (small instance)

tij_road_sml = {}   # key = (i,j), value = distance (km)

for _, dz in df_sml_dem.iterrows():
    i = dz["zone_id"]
    for _, tp in df_sml_tp.iterrows():
        j = tp["tp_id"]
        dist_km = haversine_km(tp["lon"], tp["lat"], dz["lon"], dz["lat"])
        tij_road_sml[(i, j)] = dist_km

print("Example tij_road_sml (first 5 pairs):")
for key in list(tij_road_sml.keys())[:5]:
    i, j = key
    print(f"  Zone {i} – TP {j}: {tij_road_sml[key]:.2f} km")

Example tij_road_sml (first 5 pairs):
  Zone 1.0 – TP 1.0: 1.22 km
  Zone 1.0 – TP 2.0: 0.34 km
  Zone 1.0 – TP 3.0: 2.27 km
  Zone 1.0 – TP 4.0: 1.31 km
  Zone 1.0 – TP 5.0: 2.37 km


In [7]:
# Task 1 – small instance
# Step 7: Define global cost/emission parameters and compute CT_ij and Em_ij

# Global transport cost parameters (€/unit/km)
c_road  = 0.03   # LEV last-mile
c_water = 0.01   # vessel hub -> TP

# Global emission parameters (kg CO2 / unit / km)
e_road  = 0.045
e_water = 0.015

# Maximum LV service distance (km) for small instance
D_max_sml = 2

CT_sml = {}   # transport cost per unit
Em_sml = {}   # emissions per unit

for i in I_sml:
    for j in J_sml:
        t_water = t0j_water_sml[j]
        t_road  = tij_road_sml[(i, j)]
        CT_sml[(i, j)] = c_water * t_water + c_road * t_road
        Em_sml[(i, j)] = e_water * t_water + e_road * t_road

print("Example CT_sml and Em_sml (first 5 pairs):")
for key in list(CT_sml.keys())[:5]:
    i, j = key
    print(f"  (i={i}, j={j})  CT={CT_sml[key]:.3f} €/unit  Em={Em_sml[key]:.3f} kg CO2/unit")

Example CT_sml and Em_sml (first 5 pairs):
  (i=1, j=1)  CT=0.071 €/unit  Em=0.107 kg CO2/unit
  (i=1, j=2)  CT=0.038 €/unit  Em=0.057 kg CO2/unit
  (i=1, j=3)  CT=0.117 €/unit  Em=0.175 kg CO2/unit
  (i=1, j=4)  CT=0.080 €/unit  Em=0.119 kg CO2/unit
  (i=1, j=5)  CT=0.122 €/unit  Em=0.183 kg CO2/unit


In [8]:
# Task 1 – small instance
# Step 8: Compute delta_ij (feasibility) and big-M for small instance

delta_sml = {}   # key = (i,j), value = 0 or 1

for i in I_sml:
    for j in J_sml:
        if tij_road_sml[(i, j)] <= D_max_sml:
            delta_sml[(i, j)] = 1
        else:
            delta_sml[(i, j)] = 0

# Big-M: upper bound on any y_ij. A safe choice is total demand.
M_sml = sum(d_sml.values())

print("D_max (small):", D_max_sml, "km")
print("Big-M (small):", M_sml)
print("Number of feasible (i,j) pairs (delta=1):",
      sum(delta_sml[(i, j)] for i in I_sml for j in J_sml))

D_max (small): 2 km
Big-M (small): 3121
Number of feasible (i,j) pairs (delta=1): 114


## Building the MILP model in Pyomo (small instance)

You now have all the inputs for the small instance (10 TPs, 15 demand zones). 
Start by implementing the MILP model in Pyomo for $\lambda = 1$:

<div style="background-color:#AABAB2; color: black; vertical-align: middle; padding:15px; margin: 10px; border-radius: 10px; width: 95%">
<b>Task 2: Implement the Pyomo model for the small instance (λ = 1)</b><br><br>
Translate the mathematical formulation into Pyomo code:
<ul>
<li>Create a <code>ConcreteModel</code> for the small instance</li>
<li>Define sets, parameters, decision variables</li>
<li>Define the objective function (with λ = 1)</li>
<li>Add all constraints: demand, capacity, budget, maximum TPs, service feasibility</li>
</ul>
</div>


In [9]:
# Task 2: Build the Pyomo model for the small instance (λ = 1)

from pyomo.environ import (
    ConcreteModel, Set, Param, Var, Objective, Constraint,
    Binary, NonNegativeReals, minimize
)

# Planning parameters for the small instance
B = 1000   # budget
K = 10     # maximum number of TPs
Lambda = 1  # emission penalty factor 

In [10]:
# 2.1. Create the model object
m = ConcreteModel()

# 2.2. Define index sets I and J based on I_sml and J_sml
m.I = Set(initialize=I_sml)
m.J = Set(initialize=J_sml)

# 2.3. Define parameters using the dictionaries from Task 1: demand, capacity, fixed cost, transport cost, emissions, delta (0/1 feasibility), B and K
m.d     = Param(m.I, initialize=d_sml)
m.cap   = Param(m.J, initialize=cap_sml)
m.f     = Param(m.J, initialize=f_sml)
m.CT    = Param(m.I, m.J, initialize=CT_sml)
m.Em    = Param(m.I, m.J, initialize=Em_sml)
m.delta = Param(m.I, m.J, initialize=delta_sml)

m.B = B
m.K = K
m.M = M_sml
m.Lambda = Lambda

# 2.4: Define decision variables:

m.x = Var(m.J, domain=Binary)
m.y = Var(m.I, m.J, domain=NonNegativeReals)

# 2.5: Define the objective function for λ = 1:
def obj_rule(m):
    return (
        sum(m.f[j] * m.x[j] for j in m.J)
        + sum(m.CT[i, j] * m.y[i, j] for i in m.I for j in m.J)
        + m.Lambda * sum(m.Em[i, j] * m.y[i, j] for i in m.I for j in m.J)
    )
   

m.obj = Objective(rule=obj_rule, sense=minimize)

# 2.6: Add constraints: (Demand fulfillment, TP capacity, Budget constraint, Maximum number of TPs, Service distance feasibility (big-M))

# Demand fulfillment
def demand_rule(m, i):
    return sum(m.y[i, j] for j in m.J) == m.d[i]

m.demand = Constraint(m.I, rule=demand_rule)

# TP capacity
def capacity_rule(m, j):
    return sum(m.y[i, j] for i in m.I) <= m.cap[j] * m.x[j]

m.capacity = Constraint(m.J, rule=capacity_rule)

# Budget
def budget_rule(m):
    return sum(m.f[j] * m.x[j] for j in m.J) <= m.B

m.budget = Constraint(rule=budget_rule)

# Maximum number of TPs
def max_tps_rule(m):
    return sum(m.x[j] for j in m.J) <= m.K

m.max_tps = Constraint(rule=max_tps_rule)

# Service feasibility (big-M)
def service_feas_rule(m, i, j):
    return m.y[i, j] <= m.M * m.delta[i, j]

m.service_feas = Constraint(m.I, m.J, rule=service_feas_rule)

## Solving the MILP (small instance, λ = 1)

You now have:

- a fully defined Pyomo model `m` for the **small instance**, and  
- all parameters loaded from the processed data.


<div style="background-color:#AABAB2; color: black; vertical-align: middle; padding:15px; margin: 10px; border-radius: 10px; width: 95%">
<b>Task 3: Solve and analyse the small-instance solution (λ = 1)</b><br><br>
Do the following:
<ul>
<li>Call the HiGHS solver via <code>SolverFactory("highs")</code> and solve the model <code>m</code></li>
<li>Check and print the solver status and termination condition</li>
<li>Identify which TPs are opened (values of <code>x[j]</code>)</li>
<li>For each open TP, compute how much demand it serves (sum of <code>y[i,j]</code> over all zones)</li>
<li>Verify that: all demand is satisfied and no TP exceeds its capacity</li>
<li>Compute and report: total fixed cost, total fixed cost, total emissions, total objective value</li>
</ul>
</div>


In [11]:
# Task 3: Solve and analyse the small-instance model (λ = 1)

from pyomo.environ import SolverFactory, value
import time

start_time = time.time()
# 3.1. Solve the model m, with tee=True
solver = SolverFactory("highs")
results = solver.solve(m, tee=True)

solve_time_small = time.time() - start_time
print(f"\nSolve time (small instance, λ = 1): {solve_time_small:.3f} seconds")

# 3.2. Print solver status and termination condition
print(results.solver.status)
print(results.solver.termination_condition)

# 3.3. Identify which TPs are opened
open_tps_small = [j for j in m.J if value(m.x[j]) > 0.5]
print("\nOpen TPs in small instance:", open_tps_small)

# 3.4. For each open TP j, compute total flow served: sum_i y[i,j] and compare it to cap[j]
print("\nFlow through each open TP:")
for j in open_tps_small:
    flow_j = sum(value(m.y[i, j]) for i in m.I)
    print(f"  TP {j}: total flow = {flow_j:.2f} units")

# 3.5. Check demand satisfaction for each zone:
print("\nDemand satisfaction per zone:")
for i in m.I:
    served_i = sum(value(m.y[i, j]) for j in m.J)
    print(f"  Zone {i}: demand = {value(m.d[i]):.2f}, served = {served_i:.2f}")

# 3.6. Compute cost components and emissions:
total_fixed_cost = sum(value(m.f[j]) * value(m.x[j]) for j in m.J)
total_transport_cost = sum(value(m.CT[i, j]) * value(m.y[i, j]) for i in m.I for j in m.J)
total_emissions = sum(value(m.Em[i, j]) * value(m.y[i, j]) for i in m.I for j in m.J)
total_objective = value(m.obj)

print("\nCost and emissions summary (λ = 1):")
print(f"  Total fixed cost      = {total_fixed_cost:.2f}")
print(f"  Total transport cost  = {total_transport_cost:.2f}")
print(f"  Total emissions       = {total_emissions:.2f} kg CO2")
print(f"  Total emission penalty = {(total_emissions*Lambda):.2f}")
print(f"  Objective value Z     = {total_objective:.2f}")
  


Solve time (small instance, λ = 1): 0.093 seconds
ok
optimal

Open TPs in small instance: [1, 2, 3, 4, 5, 6]

Flow through each open TP:
  TP 1: total flow = 761.00 units
  TP 2: total flow = 780.00 units
  TP 3: total flow = 395.00 units
  TP 4: total flow = 395.00 units
  TP 5: total flow = 395.00 units
  TP 6: total flow = 395.00 units

Demand satisfaction per zone:
  Zone 1: demand = 136.00, served = 136.00
  Zone 2: demand = 160.00, served = 160.00
  Zone 3: demand = 200.00, served = 200.00
  Zone 4: demand = 202.00, served = 202.00
  Zone 5: demand = 142.00, served = 142.00
  Zone 6: demand = 308.00, served = 308.00
  Zone 7: demand = 199.00, served = 199.00
  Zone 8: demand = 48.00, served = 48.00
  Zone 9: demand = 292.00, served = 292.00
  Zone 10: demand = 183.00, served = 183.00
  Zone 11: demand = 233.00, served = 233.00
  Zone 12: demand = 103.00, served = 103.00
  Zone 13: demand = 308.00, served = 308.00
  Zone 14: demand = 354.00, served = 354.00
  Zone 15: demand = 25

## Adding emission penalty and exploring different λ values

So far, you solved the small-instance model with $\lambda=1$. For larger $\lambda$, emitting more becomes more expensive, which may push the model to: change which TPs are opened, change how demand is assigned, and accept higher monetary costs in exchange for lower emissions.

In this task, you will solve the same small-instance problem for several $\lambda$ values and compare the results.

<div style="background-color:#AABAB2; color: black; vertical-align: middle; padding:15px; margin: 10px; border-radius: 10px; width: 95%">
<b>Task 4: Experiment with different λ values (small instance)</b><br><br>
Do the following:
<ul>
<li>Choose the set of λ values, e.g. <code>[1, 5, 10, 15]</code></li>
<li>For each λ:
  <ul>
    <li>build a model with that λ</li>
    <li>solve it with HiGHS</li>
    <li>record:
      <ul>
        <li>which TPs are opened</li>
        <li>total fixed cost</li>
        <li>total transport cost</li>
        <li>total emissions and emission penalty</li>
        <li>objective value</li>
      </ul>
    </li>
  </ul>
</li>
<li>Compare how the solution changes when λ increases.</li>
</ul>
<i>Hint:</i> To keep your code organised, it is convenient to write a small function that builds a model for a given λ.
</div>


In [12]:
lambda_values = [1, 5, 10, 15]
results_lambda = []

In [13]:
def build_model(lambda_value):
    """
    Build and return a Pyomo model m for a given λ,
    using the small-instance data prepared in Task 1.
    """
    m = ConcreteModel()

    # Sets
    m.I = Set(initialize=I_sml)
    m.J = Set(initialize=J_sml)

    # Parameters
    m.d     = Param(m.I, initialize=d_sml)
    m.cap   = Param(m.J, initialize=cap_sml)
    m.f     = Param(m.J, initialize=f_sml)
    m.CT    = Param(m.I, m.J, initialize=CT_sml)
    m.Em    = Param(m.I, m.J, initialize=Em_sml)
    m.delta = Param(m.I, m.J, initialize=delta_sml)

    # Planning parameters (use same B, K as before)
    m.B = B
    m.K = K
    m.M = M_sml
    m.lambda_value = lambda_value

    # Decision variables
    m.x = Var(m.J, domain=Binary)
    m.y = Var(m.I, m.J, domain=NonNegativeReals)

    # Objective
    def obj_rule(m):
        return (
            sum(m.f[j] * m.x[j] for j in m.J)
            + sum(m.CT[i, j] * m.y[i, j] for i in m.I for j in m.J)
            + m.lambda_value * sum(m.Em[i, j] * m.y[i, j] for i in m.I for j in m.J)
        )

    m.obj = Objective(rule=obj_rule, sense=minimize)

    # Constraints

    # Demand fulfillment
    def demand_rule(m, i):
        return sum(m.y[i, j] for j in m.J) == m.d[i]

    m.demand = Constraint(m.I, rule=demand_rule)

    # TP capacity
    def capacity_rule(m, j):
        return sum(m.y[i, j] for i in m.I) <= m.cap[j] * m.x[j]

    m.capacity = Constraint(m.J, rule=capacity_rule)

    # Budget
    def budget_rule(m):
        return sum(m.f[j] * m.x[j] for j in m.J) <= m.B

    m.budget = Constraint(rule=budget_rule)

    # Maximum number of TPs
    def max_tps_rule(m):
        return sum(m.x[j] for j in m.J) <= m.K

    m.max_tps = Constraint(rule=max_tps_rule)

    # Service feasibility (big-M)
    def service_feas_rule(m, i, j):
        return m.y[i, j] <= m.M * m.delta[i, j]

    m.service_feas = Constraint(m.I, m.J, rule=service_feas_rule)

    return m

In [14]:
# Loop over λ values
solver = SolverFactory("highs")

for lam in lambda_values:
    m_lam = build_model(lam)
    res = solver.solve(m_lam, tee=False)

    # Identify open TPs
    open_tps = [j for j in m_lam.J if value(m_lam.x[j]) > 0.5]

    # Cost components
    total_fixed_cost = sum(value(m_lam.f[j]) * value(m_lam.x[j]) for j in m_lam.J)
    total_transport_cost = sum(value(m_lam.CT[i, j]) * value(m_lam.y[i, j]) for i in m_lam.I for j in m_lam.J)
    total_emissions = sum(value(m_lam.Em[i, j]) * value(m_lam.y[i, j]) for i in m_lam.I for j in m_lam.J)
    total_obj = value(m_lam.obj)

    
 
    results_lambda.append({
        "lambda": lam,
        "open_tps": open_tps,
        "fixed_cost": total_fixed_cost,
        "transport_cost": total_transport_cost,
        "emissions": total_emissions,
        "objective": total_obj
    }) 

# Print summary of results
for r in results_lambda:
    print(f"λ = {r['lambda']}:")
    print(f"  Open TPs         = {r['open_tps']}")
    print(f"  Fixed cost       = {r['fixed_cost']:.2f}")
    print(f"  Transport cost   = {r['transport_cost']:.2f}")
    print(f"  Emissions        = {r['emissions']:.2f} kg CO2") 
    print(f"  Emission penalty = {r['emissions']*r['lambda']:.2f}")     
    print(f"  Objective value  = {r['objective']:.2f}\n")    

λ = 1:
  Open TPs         = [1, 2, 3, 4, 5, 6]
  Fixed cost       = 800.00
  Transport cost   = 180.15
  Emissions        = 270.22 kg CO2
  Emission penalty = 270.22
  Objective value  = 1250.37

λ = 5:
  Open TPs         = [1, 2, 3, 4, 5, 6]
  Fixed cost       = 800.00
  Transport cost   = 180.15
  Emissions        = 270.22 kg CO2
  Emission penalty = 1351.10
  Objective value  = 2331.24

λ = 10:
  Open TPs         = [1, 2, 3, 4, 5, 6, 10]
  Fixed cost       = 900.00
  Transport cost   = 173.33
  Emissions        = 259.99 kg CO2
  Emission penalty = 2599.89
  Objective value  = 3673.21

λ = 15:
  Open TPs         = [1, 2, 3, 4, 5, 6, 9, 10]
  Fixed cost       = 1000.00
  Transport cost   = 168.54
  Emissions        = 252.81 kg CO2
  Emission penalty = 3792.16
  Objective value  = 4960.70



## Scaling up: large instance and runtime comparison

So far, you have built and solved the small instance (10 TPs, 15 demand zones) and recorded its solve time.

We now consider a **larger instance** with: 36 candidate TPs and 300 HoReCa demand zones. The model structure is exactly the same, but the number of decision variables and constraints increases and the MILP becomes harder to solve. 

The main goal of this task is to see how the solver runtime changes when the problem size increases. We will **not** re-experiment with different λ values here; we use a single λ = 1.

<div style="background-color:#AABAB2; color: black; vertical-align: middle; padding:15px; margin: 10px; border-radius: 10px; width: 95%">
<b>Task 5: Solve the large instance and compare runtimes</b><br><br>
Do the following:
<ul>
<li>Load and compute the large-instance data (similar to task 1)</li>
<li>Build a new Pyomo model for the large instance:
  <ul>
    <li>Use the same structure as before (same component names <code>m.I</code>, <code>m.J</code>, <code>m.x</code>, <code>m.y</code>, etc.)</li>
    <li>Use a single λ value (λ = 1)</li>
  </ul>
</li>
<li>Solve the large-instance model with HiGHS and record the solve time</li>
<li>Compare:
  <ul>
    <li>small vs large solve time</li>
    <li>How many TPs are opened in each case</li>
    <li>Any noticeable differences in model behaviour</li>
  </ul>
</li>
</ul>
</div>


In [15]:
# Task 5 – large instance
# Step 1: Load the large-instance data (demand zones + TPs)

data_file = "GA_2_5_data.xlsx"

df_lg_dem = pd.read_excel(data_file, sheet_name="Large_Demand")
df_lg_tp  = pd.read_excel(data_file, sheet_name="Large_TP")

df_lg_dem = df_lg_dem.rename(columns={
    "number": "zone_id",
    "latitude": "lat",
    "longitude": "lon",
    "demand": "demand"
})

df_lg_tp = df_lg_tp.rename(columns={
    "number": "tp_id",
    "latitude": "lat",
    "longitude": "lon",
    "capacity": "capacity",
    "establishment_cost": "fixed_cost"
})

I_large = df_lg_dem["zone_id"].tolist()
J_large = df_lg_tp["tp_id"].tolist()

d_large   = dict(zip(df_lg_dem["zone_id"], df_lg_dem["demand"]))
cap_large = dict(zip(df_lg_tp["tp_id"], df_lg_tp["capacity"]))
f_large   = dict(zip(df_lg_tp["tp_id"], df_lg_tp["fixed_cost"]))

print("Large instance – |I| =", len(I_large), ", |J| =", len(J_large))

Large instance – |I| = 300 , |J| = 36


In [16]:
# Task 5 – large instance
# Step 2: Compute distances (water + road), CT_ij, Em_ij, delta_ij, M for large instance

# Water distances hub -> TP
t0j_water_large = {}
for _, row in df_lg_tp.iterrows():
    j = row["tp_id"]
    dist_km = haversine_km(hub_lon, hub_lat, row["lon"], row["lat"])
    t0j_water_large[j] = dist_km

# Road distances TP -> demand zone
tij_road_large = {}
for _, dz in df_lg_dem.iterrows():
    i = dz["zone_id"]
    for _, tp in df_lg_tp.iterrows():
        j = tp["tp_id"]
        dist_km = haversine_km(tp["lon"], tp["lat"], dz["lon"], dz["lat"])
        tij_road_large[(i, j)] = dist_km

        
D_max_large = 2

CT_large = {}
Em_large = {}
delta_large = {}

for i in I_large:
    for j in J_large:
        t_water = t0j_water_large[j]
        t_road  = tij_road_large[(i, j)]
        CT_large[(i, j)] = c_water * t_water + c_road * t_road
        Em_large[(i, j)] = e_water * t_water + e_road * t_road
        delta_large[(i, j)] = 1 if t_road <= D_max_large else 0

M_large = sum(d_large.values())

print("D_max (large):", D_max_large, "km")
print("Big-M (large):", M_large)
print("Feasible (i,j) pairs (delta=1):",
      sum(delta_large[(i, j)] for i in I_large for j in J_large))


D_max (large): 2 km
Big-M (large): 3121
Feasible (i,j) pairs (delta=1): 9200


In [17]:
# Task 5 – large instance
# Step 3: Build and solve the large-instance model

B_large = 2000   
K_large = 20 
lambda_large = 1


m_large = ConcreteModel()

# Sets
m_large.I = Set(initialize=I_large)
m_large.J = Set(initialize=J_large)

# Parameters
m_large.d     = Param(m_large.I, initialize=d_large)
m_large.cap   = Param(m_large.J, initialize=cap_large)
m_large.f     = Param(m_large.J, initialize=f_large)
m_large.CT    = Param(m_large.I, m_large.J, initialize=CT_large)
m_large.Em    = Param(m_large.I, m_large.J, initialize=Em_large)
m_large.delta = Param(m_large.I, m_large.J, initialize=delta_large)

m_large.B = B_large
m_large.K = K_large
m_large.M = M_large

m_large.Lambda = lambda_large

# Variables
m_large.x = Var(m_large.J, domain=Binary)
m_large.y = Var(m_large.I, m_large.J, domain=NonNegativeReals)

# Objective
def obj_large_rule(m):
    return (
        sum(m.f[j] * m.x[j] for j in m.J)
        + sum(m.CT[i, j] * m.y[i, j] for i in m.I for j in m.J)
        + m.Lambda * sum(m.Em[i, j] * m.y[i, j] for i in m.I for j in m.J)
    )

m_large.obj = Objective(rule=obj_large_rule, sense=minimize)

# Constraints
# Demand fulfillment
def demand_large_rule(m, i):
    return sum(m.y[i, j] for j in m.J) == m.d[i]

m_large.demand = Constraint(m_large.I, rule=demand_large_rule)

# TP capacity
def capacity_large_rule(m, j):
    return sum(m.y[i, j] for i in m.I) <= m.cap[j] * m.x[j]

m_large.capacity = Constraint(m_large.J, rule=capacity_large_rule)

# Budget
def budget_large_rule(m):
    return sum(m.f[j] * m.x[j] for j in m.J) <= m.B

m_large.budget = Constraint(rule=budget_large_rule)

# Maximum number of TPs
def max_tps_large_rule(m):
    return sum(m.x[j] for j in m.J) <= m.K

m_large.max_tps = Constraint(rule=max_tps_large_rule)

# Service feasibility (big-M)
def service_feas_large_rule(m, i, j):
    return m.y[i, j] <= m.M * m.delta[i, j]

m_large.service_feas = Constraint(m_large.I, m_large.J, rule=service_feas_large_rule)

start_time_large = time.time()
# Solve and measure runtime
solver_large = SolverFactory("highs")
results_large = solver_large.solve(m_large, tee=False)

solve_time_large = time.time() - start_time_large
print(f"\nSolve time (large instance, λ = {lambda_large}): {solve_time_large:.3f} seconds")



Solve time (large instance, λ = 1): 66.261 seconds


In [18]:
# Task 5 – large instance
# Step 4: Basic comparison with small instance

open_tps_large = [j for j in m_large.J if value(m_large.x[j]) > 0.5]
print("\nOpen TPs in large instance:", open_tps_large)

total_obj_large = value(m_large.obj)
print(f"Objective value (large instance) = {total_obj_large:.2f}")

print("\nRuntime comparison:")
print(f"  Small instance solve time: {solve_time_small:.3f} seconds")
print(f"  Large instance solve time: {solve_time_large:.3f} seconds")


Open TPs in large instance: [1, 2, 3, 4, 11, 12, 14, 15, 19, 22, 27]
Objective value (large instance) = 1886.69

Runtime comparison:
  Small instance solve time: 0.093 seconds
  Large instance solve time: 66.261 seconds


> By Nadia Pourmohammadzia and Gonçalo Homen de Almeida Correia, Delft University of Technology. CC BY 4.0, more info [on the Credits page of Workbook](https://mude.citg.tudelft.nl/workbook-2025/credits.html)